# Описание задачи


Многие знают про маркетплейсы где продаются б/у вещи, на которых есть возможность недорого купить качественную и полезную вещь. Но всегда волнует вопрос - кто и как устанавливает цену, и какие его характеристики больше всего влияют на итоговую стоимость продажи?! Вопрос становиться особо актуальным, если речь идет про дорогие товары, например про автомобили!    

В рамках данного исследования будет вестить работа с данными о продажах автомобилей на вторичном рынке. 

**Целью проекта будет *разработанная модель* предсказания стоимости автомобиля на вторичном рынке.**


## Данные
**train.csv** - информация о продажах (~440000) автомобилей с аукционов, которые будут использоваться в качестве обучающих данных.

**test.csv** - информация о продажах (~110000) автомобилей с аукционов, которые будут использоваться в качестве тестовых данных. Ваша задача - предсказать значение 'sellingprice' для каждого автомобиля из этого датасета.

**sample_submission.csv** - файл предсказаний в правильном формате.
vin - идентификатор каждого автомобиля в тестовом наборе.
sellingprice - Целевой признак. Для каждого автомобиля предскажите числовое значение стоимости автомобиля.

## Описание полей данных
`year` - год производства

`make` - производитель

`model` - модель

`trim` - модификация

`body` - тип кузова

`transmission` - тип КПП

`vin` - идентификатор (вин)

`state` - штат регистрации

`condition` - состояние по шкале (1-5)

`odometer` - пробег в милях

`color` - цвет кузова

`interior` - цвет интерьера

`seller` - продавец

`sellingprice` - стоимость продажи

`saledate` - дата продажи

## Ход решения задачи

Пошагово:

1. загрузка и ознакомление с данными,
2. предварительная обработка,
3. полноценный разведочный анализ,
4. разработка новых синтетических признаков,
5. проверка на мультиколлинеарность,
6. отбор финального набора обучающих признаков,
7. выбор и обучение моделей,
8. итоговая оценка качества предсказания лучшей модели,
9. анализ важности ее признаков.

### 1. Загрузка и ознакомление с данными

In [1]:
!pip install category_encoders -U

In [2]:
!pip install catboost -U

In [3]:
#импортируем необходимые для работы библиотеки
import pandas as pd
pd.set_option
pd.options.mode.chained_assignment = None
import matplotlib.pyplot as plt 
import numpy as np
import seaborn as sns

import catboost
from catboost import CatBoostRegressor
from catboost import Pool, cv

from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import cross_validate

from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor
from sklearn.linear_model import LinearRegression

from sklearn.preprocessing import OrdinalEncoder

from sklearn.experimental import enable_iterative_imputer
from sklearn.impute import SimpleImputer
from sklearn.impute import IterativeImputer

from sklearn.base import TransformerMixin

from sklearn.metrics import accuracy_score
from sklearn.metrics import precision_score
from sklearn.metrics import recall_score
from sklearn.metrics import f1_score
from sklearn.metrics import roc_auc_score
from sklearn.metrics import recall_score
from sklearn.metrics import mean_absolute_percentage_error as mape

После загрузки необходимых библиотек подгрузим датасеты

In [4]:
df_train = pd.read_csv('/Users/moygospodin/Documents/Practicum/Projects/Automobile_research/datasets/train.csv')
df_test = pd.read_csv('/Users/moygospodin/Documents/Practicum/Projects/Automobile_research/datasets/test.csv')

Проверим, что все отображается верно

In [5]:
display(df_train.head(5))
display(df_test.head(5))

year    make   model    trim   body transmission                vin state  \
0  2011    Ford    Edge     SEL    suv    automatic  2fmdk3jc4bba41556    md   
1  2014    Ford  Fusion      SE  Sedan    automatic  3fa6p0h75er208976    mo   
2  2012  Nissan  Sentra  2.0 SL  sedan    automatic  3n1ab6ap4cl698412    nj   
3  2003  HUMMER      H2    Base    suv    automatic  5grgn23u93h101360    tx   
4  2007    Ford  Fusion     SEL  Sedan    automatic  3fahp08z17r268380    md   

   condition  odometer  color interior                      seller  \
0        4.2  111041.0  black    black          santander consumer   
1        3.5   31034.0  black    black       ars/avis budget group   
2        2.2   35619.0  black    black          nissan-infiniti lt   
3        2.8  131301.0   gold    beige  wichita falls ford lin inc   
4        2.0  127709.0  black    black                purple heart   

   sellingprice                                 saledate  
0         12500  Tue Jun 02 2015 02:30:00 GMT-0700 (PDT)  
1         14500  Wed Feb 25 2015 02:00:00 GMT-0800 (PST)  
2          9100  Wed Jun 10 2015 02:30:00 GMT-0700 (PDT)  
3         13300  Wed Jun 17 2015 03:00:00 GMT-0700 (PDT)  
4          1300  Tue Feb 03 2015 04:00:00 GMT-0800 (PST)

year       make         model      trim      body transmission  \
0  2005   Cadillac           CTS      Base     Sedan    automatic   
1  2014        GMC  Savana Cargo      2500       Van          NaN   
2  2013     Nissan        Murano         S       SUV    automatic   
3  2013  Chevrolet        Impala  LS Fleet     Sedan    automatic   
4  2013     Nissan         Titan        SV  Crew Cab    automatic   

                 vin state  condition  odometer   color interior  \
0  1g6dp567450124779    ca        2.7  116970.0  silver    black   
1  1gtw7fca7e1902207    pa        4.4    6286.0   white     gray   
2  jn8az1mw6dw303497    oh        4.6   11831.0    gray    black   
3  2g1wf5e34d1160703    fl        2.3   57105.0  silver    black   
4  1n6aa0ec3dn301209    tn        2.9   31083.0   black    black   

                                             seller  \
0                            lexus of stevens creek   
1                                            u-haul   
2                                nissan-infiniti lt   
3  onemain rem/auto club of miami inc dba north dad   
4                         nissan north america inc.   

                                  saledate  
0  Wed Jan 14 2015 04:30:00 GMT-0800 (PST)  
1  Fri Feb 27 2015 01:00:00 GMT-0800 (PST)  
2  Tue Feb 24 2015 01:30:00 GMT-0800 (PST)  
3  Fri Mar 06 2015 02:00:00 GMT-0800 (PST)  
4  Wed Jun 03 2015 03:30:00 GMT-0700 (PDT)

### 2. Предобработка данных

Нужно посмотреть, все ли данные корректны в датасетах. Удалить дубликаты, если таковые имеются и убрать столбцы с данными, которые либо дублируют друг друга, либо не помогут в выполнении задачи. Проверить на выбросы и пропуски в данных.


In [6]:
for i in [df_train, df_test]:
    display(i.info())
    display(i.isna().sum())
    display(i.duplicated().sum())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 440236 entries, 0 to 440235
Data columns (total 15 columns):
 #   Column        Non-Null Count   Dtype  
---  ------        --------------   -----  
 0   year          440236 non-null  int64  
 1   make          432193 non-null  object 
 2   model         432113 non-null  object 
 3   trim          431899 non-null  object 
 4   body          429843 non-null  object 
 5   transmission  388775 non-null  object 
 6   vin           440236 non-null  object 
 7   state         440236 non-null  object 
 8   condition     430831 non-null  float64
 9   odometer      440167 non-null  float64
 10  color         439650 non-null  object 
 11  interior      439650 non-null  object 
 12  seller        440236 non-null  object 
 13  sellingprice  440236 non-null  int64  
 14  saledate      440236 non-null  object 
dtypes: float64(2), int64(2), object(11)
memory usage: 50.4+ MB


None

year                0
make             8043
model            8123
trim             8337
body            10393
transmission    51461
vin                 0
state               0
condition        9405
odometer           69
color             586
interior          586
seller              0
sellingprice        0
saledate            0
dtype: int64

0

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 110060 entries, 0 to 110059
Data columns (total 14 columns):
 #   Column        Non-Null Count   Dtype  
---  ------        --------------   -----  
 0   year          110060 non-null  int64  
 1   make          107999 non-null  object 
 2   model         107981 non-null  object 
 3   trim          107946 non-null  object 
 4   body          107466 non-null  object 
 5   transmission  97048 non-null   object 
 6   vin           110060 non-null  object 
 7   state         110060 non-null  object 
 8   condition     107681 non-null  float64
 9   odometer      110041 non-null  float64
 10  color         109902 non-null  object 
 11  interior      109902 non-null  object 
 12  seller        110060 non-null  object 
 13  saledate      110060 non-null  object 
dtypes: float64(2), int64(1), object(11)
memory usage: 11.8+ MB


None

year                0
make             2061
model            2079
trim             2114
body             2594
transmission    13012
vin                 0
state               0
condition        2379
odometer           19
color             158
interior          158
seller              0
saledate            0
dtype: int64

0

везде нижний регистр

In [7]:
df_train['saledate'] = pd.to_datetime(df_train['saledate'], utc=True)

In [8]:
df_test['saledate'] = pd.to_datetime(df_test['saledate'], utc=True)

In [9]:
df_train = df_train.applymap(lambda s: s.lower() if type(s) == str else s)
df_test = df_test.applymap(lambda s: s.lower() if type(s) == str else s)

In [10]:
for i in df_train.columns:
    display(df_train[i].value_counts())

2012    80625
2013    77566
2014    64225
2011    38115
2008    24646
2007    24152
2006    21118
2010    20647
2005    16794
2009    16064
2004    13658
2003    10512
2002     7726
2015     7462
2001     5147
2000     4161
1999     2658
1998     1747
1997     1224
1996      683
1995      567
1994      319
1993      168
1992      103
1991       56
1990       38
1989       15
1988       11
1985       10
1986        8
1987        5
1984        4
1983        1
1982        1
Name: year, dtype: int64

ford         74067
chevrolet    47818
nissan       42866
toyota       31711
dodge        24294
             ...  
daewoo           1
dodge tk         1
mazda tk         1
dot              1
airstream        1
Name: make, Length: 62, dtype: int64

altima            15454
f-150             11408
fusion            10244
camry             10000
escape             9447
                  ...  
420-class             1
c230                  1
rrs                   1
activehybrid 5        1
g500                  1
Name: model, Length: 839, dtype: int64

base                43876
se                  34498
lx                  16511
limited             14516
lt                  13431
                    ...  
cl65 amg                1
cargo awd w/yf7         1
gr tr gr touring        1
sub 4x4 v8              1
4x4 v6 xlt sport        1
Name: trim, Length: 1850, dtype: int64

sedan                      190861
suv                        113042
hatchback                   20715
minivan                     20114
coupe                       13896
crew cab                    12823
wagon                       12600
convertible                  8183
supercrew                    7081
g sedan                      5859
supercab                     4143
regular cab                  3861
van                          3544
extended cab                 3500
quad cab                     3208
e-series van                 1426
g coupe                      1282
double cab                   1260
crewmax cab                   429
king cab                      418
g convertible                 251
access cab                    232
genesis coupe                 221
club cab                      141
koup                          135
cts coupe                     115
mega cab                       94
elantra coupe                  74
beetle convertible             52
promaster carg

...

black        87115
white        84149
silver       65667
gray         65284
blue         40237
red          34514
—            19520
green         8975
gold          8934
beige         7257
burgundy      7059
brown         5320
orange        1629
purple        1250
off-white     1143
yellow         979
charcoal       389
turquoise      183
pink            32
lime            14
Name: color, dtype: int64

black        192442
gray         140843
beige         46878
tan           34709
—             13563
brown          6818
red            1070
blue            885
silver          844
off-white       373
purple          276
gold            256
white           215
green           198
burgundy        155
orange          109
yellow           16
Name: interior, dtype: int64

nissan-infiniti lt                15823
ford motor credit company,llc     15276
the hertz corporation             14692
santander consumer                12230
avis corporation                  10098
                                  ...  
bay shore motors                      1
thrifty rent a car systems inc        1
volvo of wichita                      1
wright way hyundai                    1
studio city auto group                1
Name: seller, Length: 13025, dtype: int64

11000    3510
12000    3499
13000    3374
10000    3178
14000    3104
         ... 
57100       1
73100       1
41501       1
66700       1
2725        1
Name: sellingprice, Length: 1735, dtype: int64

2015-02-09 17:30:00+00:00    4209
2015-01-26 17:30:00+00:00    3878
2015-02-16 17:30:00+00:00    3862
2015-01-19 17:30:00+00:00    3777
2015-03-02 17:30:00+00:00    3633
                             ... 
2015-01-06 21:10:00+00:00       1
2015-06-24 20:35:00+00:00       1
2015-06-16 23:15:00+00:00       1
2015-04-01 02:31:00+00:00       1
2015-05-19 18:30:00+00:00       1
Name: saledate, Length: 3597, dtype: int64

Заполняем пропуски

In [11]:
class DataFrameImputer(TransformerMixin):

    def __init__(self):
        """Impute missing values.

        Columns of dtype object are imputed with the most frequent value 
        in column.

        Columns of other types are imputed with mean of column.

        """
    def fit(self, X, y=None):

        self.fill = pd.Series([X[c].value_counts().index[0]
            if X[c].dtype == np.dtype('O') else X[c].mean() for c in X],
            index=X.columns)

        return self

    def transform(self, X, y=None):
        return X.fillna(self.fill)

In [12]:
df_train_fill = DataFrameImputer().fit_transform(df_train)

In [13]:
df_test_fill = DataFrameImputer().fit_transform(df_test)

In [14]:
df_train_fill.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 440236 entries, 0 to 440235
Data columns (total 15 columns):
 #   Column        Non-Null Count   Dtype              
---  ------        --------------   -----              
 0   year          440236 non-null  int64              
 1   make          440236 non-null  object             
 2   model         440236 non-null  object             
 3   trim          440236 non-null  object             
 4   body          440236 non-null  object             
 5   transmission  440236 non-null  object             
 6   vin           440236 non-null  object             
 7   state         440236 non-null  object             
 8   condition     440236 non-null  float64            
 9   odometer      440236 non-null  float64            
 10  color         440236 non-null  object             
 11  interior      440236 non-null  object             
 12  seller        440236 non-null  object             
 13  sellingprice  440236 non-null  int64        

In [15]:
%%time
#тут работает энкодер
data = pd.DataFrame(OrdinalEncoder().fit_transform(df_train_fill),
                            columns=df_train_fill.columns)

CPU times: user 6.64 s, sys: 188 ms, total: 6.82 s
Wall time: 7.08 s


In [16]:
%%time
#тут работает энкодер
data_test = pd.DataFrame(OrdinalEncoder().fit_transform(df_test_fill),
                            columns=df_test_fill.columns)

CPU times: user 1.59 s, sys: 54.8 ms, total: 1.64 s
Wall time: 1.75 s


In [17]:
#data.info()

In [18]:
#features_train = df_train_fill.drop(['sellingprice'], axis=1)
#target_train = df_train_fill['sellingprice']

#features_test = df_test_fill


features_train = data.drop(['sellingprice'], axis=1)
target_train = data['sellingprice']

features_test = data_test


In [19]:
features_train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 440236 entries, 0 to 440235
Data columns (total 14 columns):
 #   Column        Non-Null Count   Dtype  
---  ------        --------------   -----  
 0   year          440236 non-null  float64
 1   make          440236 non-null  float64
 2   model         440236 non-null  float64
 3   trim          440236 non-null  float64
 4   body          440236 non-null  float64
 5   transmission  440236 non-null  float64
 6   vin           440236 non-null  float64
 7   state         440236 non-null  float64
 8   condition     440236 non-null  float64
 9   odometer      440236 non-null  float64
 10  color         440236 non-null  float64
 11  interior      440236 non-null  float64
 12  seller        440236 non-null  float64
 13  saledate      440236 non-null  float64
dtypes: float64(14)
memory usage: 47.0 MB


In [20]:
cat = CatBoostRegressor(#cat_features = [1,2,3,4,5,6,7,10,11,12,13],
                        loss_function = "RMSE",
                       eval_metric = "RMSE",
                       random_state=1602)
cat_features = [1,2,3,4,5,6,7,10,11,12,13]

In [21]:
%%time
params = {'depth': [4, 6, 10],
          'learning_rate' : [0.05, 0.1, 0.15],
          'l2_leaf_reg': [1,4,9],
          'iterations': [1000],
           'early_stopping_rounds':[800]
#           'loss_function':['MultiClass'],
          
         }

cb = cat
cb_b = GridSearchCV(cb, param_grid=params,
                      scoring='neg_mean_absolute_percentage_error', n_jobs=-1, cv=3)
cb_b.fit(features_train, target_train)


0:	learn: 284.2399775	total: 236ms	remaining: 3m 55s
1:	learn: 277.0380288	total: 346ms	remaining: 2m 52s
2:	learn: 270.4258832	total: 444ms	remaining: 2m 27s
3:	learn: 264.2096619	total: 503ms	remaining: 2m 5s
4:	learn: 258.0990819	total: 570ms	remaining: 1m 53s
5:	learn: 252.4307461	total: 654ms	remaining: 1m 48s
6:	learn: 247.0026887	total: 786ms	remaining: 1m 51s
7:	learn: 241.9958287	total: 974ms	remaining: 2m
8:	learn: 237.3242818	total: 1.05s	remaining: 1m 56s
9:	learn: 232.8998714	total: 1.13s	remaining: 1m 51s
10:	learn: 228.5778900	total: 1.2s	remaining: 1m 47s
11:	learn: 224.4528560	total: 1.26s	remaining: 1m 44s
12:	learn: 220.7003642	total: 1.4s	remaining: 1m 46s
13:	learn: 217.1778210	total: 1.48s	remaining: 1m 44s
14:	learn: 213.8935585	total: 1.56s	remaining: 1m 42s
15:	learn: 210.9120029	total: 1.64s	remaining: 1m 40s
16:	learn: 207.9026438	total: 1.75s	remaining: 1m 41s
17:	learn: 205.0090505	total: 1.82s	remaining: 1m 39s
18:	learn: 202.3275195	total: 1.87s	remaining

0:	learn: 277.1346230	total: 254ms	remaining: 4m 13s
1:	learn: 263.7884278	total: 330ms	remaining: 2m 44s
2:	learn: 251.7997904	total: 400ms	remaining: 2m 13s
3:	learn: 240.9426308	total: 474ms	remaining: 1m 57s
4:	learn: 231.6749155	total: 573ms	remaining: 1m 53s
5:	learn: 223.7513012	total: 682ms	remaining: 1m 53s
6:	learn: 216.2062627	total: 825ms	remaining: 1m 57s
7:	learn: 209.6830779	total: 936ms	remaining: 1m 56s
8:	learn: 203.6620272	total: 1s	remaining: 1m 50s
9:	learn: 198.4682016	total: 1.07s	remaining: 1m 46s
10:	learn: 194.0883722	total: 1.12s	remaining: 1m 40s
11:	learn: 190.3053781	total: 1.19s	remaining: 1m 37s
12:	learn: 187.0430028	total: 1.25s	remaining: 1m 35s
13:	learn: 183.7989867	total: 1.37s	remaining: 1m 36s
14:	learn: 180.9916461	total: 1.45s	remaining: 1m 35s
15:	learn: 178.5570738	total: 1.53s	remaining: 1m 34s
16:	learn: 176.4072132	total: 1.59s	remaining: 1m 32s
17:	learn: 174.3203623	total: 1.67s	remaining: 1m 30s
18:	learn: 172.4821483	total: 1.75s	remai

305:	learn: 111.9374559	total: 20.7s	remaining: 47s
306:	learn: 111.7975778	total: 20.8s	remaining: 47s
307:	learn: 111.6953202	total: 20.9s	remaining: 46.9s
308:	learn: 111.5575793	total: 20.9s	remaining: 46.8s
309:	learn: 111.5129514	total: 21s	remaining: 46.7s
310:	learn: 111.4504071	total: 21s	remaining: 46.6s
311:	learn: 111.3691164	total: 21.1s	remaining: 46.5s
312:	learn: 111.2608624	total: 21.2s	remaining: 46.4s
313:	learn: 111.1524123	total: 21.2s	remaining: 46.4s
314:	learn: 111.0680775	total: 21.3s	remaining: 46.3s
315:	learn: 111.0290708	total: 21.3s	remaining: 46.2s
316:	learn: 110.9291681	total: 21.4s	remaining: 46.1s
317:	learn: 110.8363896	total: 21.5s	remaining: 46s
318:	learn: 110.7352935	total: 21.5s	remaining: 46s
319:	learn: 110.6380681	total: 21.6s	remaining: 45.9s
320:	learn: 110.5430616	total: 21.7s	remaining: 45.8s
321:	learn: 110.4867158	total: 21.7s	remaining: 45.7s
322:	learn: 110.4208897	total: 21.8s	remaining: 45.6s
323:	learn: 110.3681342	total: 21.9s	rem

305:	learn: 112.0103988	total: 20.8s	remaining: 47.3s
306:	learn: 111.8735646	total: 20.9s	remaining: 47.2s
307:	learn: 111.8269098	total: 21s	remaining: 47.1s
308:	learn: 111.6333123	total: 21s	remaining: 47s
309:	learn: 111.4959429	total: 21.1s	remaining: 46.9s
310:	learn: 111.4283660	total: 21.1s	remaining: 46.8s
311:	learn: 111.3700084	total: 21.2s	remaining: 46.8s
312:	learn: 111.1946286	total: 21.3s	remaining: 46.7s
313:	learn: 111.0677081	total: 21.3s	remaining: 46.6s
314:	learn: 111.0248510	total: 21.4s	remaining: 46.5s
315:	learn: 110.9775990	total: 21.4s	remaining: 46.4s
316:	learn: 110.9429174	total: 21.5s	remaining: 46.3s
317:	learn: 110.8482061	total: 21.5s	remaining: 46.2s
318:	learn: 110.7667894	total: 21.6s	remaining: 46.2s
319:	learn: 110.7351159	total: 21.7s	remaining: 46s
320:	learn: 110.6395949	total: 21.7s	remaining: 46s
321:	learn: 110.5582087	total: 21.8s	remaining: 45.9s
322:	learn: 110.4255009	total: 21.9s	remaining: 45.8s
323:	learn: 110.3309585	total: 21.9s	r

307:	learn: 95.1913100	total: 20.9s	remaining: 46.9s
308:	learn: 95.0522833	total: 20.9s	remaining: 46.8s
309:	learn: 95.0015951	total: 21s	remaining: 46.7s
310:	learn: 94.9676542	total: 21.1s	remaining: 46.6s
311:	learn: 94.9457758	total: 21.1s	remaining: 46.5s
312:	learn: 94.9181120	total: 21.2s	remaining: 46.4s
313:	learn: 94.8782812	total: 21.2s	remaining: 46.4s
314:	learn: 94.7409539	total: 21.3s	remaining: 46.3s
315:	learn: 94.6939687	total: 21.4s	remaining: 46.2s
316:	learn: 94.5999747	total: 21.4s	remaining: 46.2s
317:	learn: 94.5511615	total: 21.5s	remaining: 46.1s
318:	learn: 94.4518002	total: 21.5s	remaining: 46s
319:	learn: 94.3603571	total: 21.6s	remaining: 45.9s
320:	learn: 94.2493906	total: 21.7s	remaining: 45.8s
321:	learn: 94.1729424	total: 21.7s	remaining: 45.7s
322:	learn: 94.0720372	total: 21.8s	remaining: 45.6s
323:	learn: 94.0215452	total: 21.8s	remaining: 45.5s
324:	learn: 93.9843518	total: 21.9s	remaining: 45.4s
325:	learn: 93.9466176	total: 21.9s	remaining: 45.

...

464:	learn: 52.5496365	total: 1m	remaining: 1m 9s
465:	learn: 52.5230720	total: 1m	remaining: 1m 9s
466:	learn: 52.5125310	total: 1m	remaining: 1m 9s
467:	learn: 52.4919329	total: 1m 1s	remaining: 1m 9s
468:	learn: 52.4655432	total: 1m 1s	remaining: 1m 9s
469:	learn: 52.4468741	total: 1m 1s	remaining: 1m 9s
470:	learn: 52.4326470	total: 1m 1s	remaining: 1m 9s
471:	learn: 52.4109950	total: 1m 1s	remaining: 1m 8s
472:	learn: 52.3730125	total: 1m 1s	remaining: 1m 8s
473:	learn: 52.3626129	total: 1m 1s	remaining: 1m 8s
474:	learn: 52.3362482	total: 1m 1s	remaining: 1m 8s
475:	learn: 52.3222613	total: 1m 2s	remaining: 1m 8s
476:	learn: 52.3022950	total: 1m 2s	remaining: 1m 8s
477:	learn: 52.2849195	total: 1m 2s	remaining: 1m 7s
478:	learn: 52.2670920	total: 1m 2s	remaining: 1m 7s
479:	learn: 52.2438970	total: 1m 2s	remaining: 1m 7s
480:	learn: 52.2262537	total: 1m 2s	remaining: 1m 7s
481:	learn: 52.2164510	total: 1m 2s	remaining: 1m 7s
482:	learn: 52.2004029	total: 1m 2s	remaining: 1m 7s
48

619:	learn: 49.8551642	total: 1m 20s	remaining: 49.1s
620:	learn: 49.8438658	total: 1m 20s	remaining: 49s
621:	learn: 49.8343068	total: 1m 20s	remaining: 48.9s
622:	learn: 49.8191128	total: 1m 20s	remaining: 48.7s
623:	learn: 49.8029342	total: 1m 20s	remaining: 48.6s
624:	learn: 49.7831227	total: 1m 20s	remaining: 48.5s
625:	learn: 49.7672706	total: 1m 20s	remaining: 48.3s
626:	learn: 49.7373990	total: 1m 21s	remaining: 48.2s
627:	learn: 49.7248089	total: 1m 21s	remaining: 48.1s
628:	learn: 49.7110927	total: 1m 21s	remaining: 47.9s
629:	learn: 49.7027475	total: 1m 21s	remaining: 47.9s
630:	learn: 49.6919581	total: 1m 21s	remaining: 47.8s
631:	learn: 49.6837832	total: 1m 21s	remaining: 47.7s
632:	learn: 49.6585019	total: 1m 22s	remaining: 47.5s
633:	learn: 49.6386523	total: 1m 22s	remaining: 47.4s
634:	learn: 49.6315843	total: 1m 22s	remaining: 47.3s
635:	learn: 49.6215020	total: 1m 22s	remaining: 47.2s
636:	learn: 49.6089528	total: 1m 22s	remaining: 47.1s
637:	learn: 49.6026667	total: 

772:	learn: 47.9721746	total: 1m 39s	remaining: 29.2s
773:	learn: 47.9618552	total: 1m 39s	remaining: 29.1s
774:	learn: 47.9521678	total: 1m 39s	remaining: 29s
775:	learn: 47.9414916	total: 1m 39s	remaining: 28.8s
776:	learn: 47.9350379	total: 1m 40s	remaining: 28.7s
777:	learn: 47.9284664	total: 1m 40s	remaining: 28.6s
778:	learn: 47.9224269	total: 1m 40s	remaining: 28.5s
779:	learn: 47.9105294	total: 1m 40s	remaining: 28.3s
780:	learn: 47.8994076	total: 1m 40s	remaining: 28.2s
781:	learn: 47.8878574	total: 1m 40s	remaining: 28.1s
782:	learn: 47.8761431	total: 1m 40s	remaining: 27.9s
783:	learn: 47.8583795	total: 1m 40s	remaining: 27.8s
784:	learn: 47.8406123	total: 1m 40s	remaining: 27.7s
785:	learn: 47.8266087	total: 1m 41s	remaining: 27.5s
786:	learn: 47.8174521	total: 1m 41s	remaining: 27.4s
787:	learn: 47.8067957	total: 1m 41s	remaining: 27.3s
788:	learn: 47.7981914	total: 1m 41s	remaining: 27.1s
789:	learn: 47.7915299	total: 1m 41s	remaining: 27s
790:	learn: 47.7780001	total: 1m

926:	learn: 46.4423883	total: 1m 58s	remaining: 9.36s
927:	learn: 46.4295463	total: 1m 59s	remaining: 9.23s
928:	learn: 46.4224850	total: 1m 59s	remaining: 9.11s
929:	learn: 46.4148073	total: 1m 59s	remaining: 8.98s
930:	learn: 46.4069670	total: 1m 59s	remaining: 8.85s
931:	learn: 46.4004623	total: 1m 59s	remaining: 8.72s
932:	learn: 46.3864428	total: 1m 59s	remaining: 8.6s
933:	learn: 46.3781733	total: 1m 59s	remaining: 8.47s
934:	learn: 46.3718497	total: 1m 59s	remaining: 8.34s
935:	learn: 46.3610276	total: 2m	remaining: 8.21s
936:	learn: 46.3508847	total: 2m	remaining: 8.08s
937:	learn: 46.3403703	total: 2m	remaining: 7.95s
938:	learn: 46.3328453	total: 2m	remaining: 7.82s
939:	learn: 46.3248140	total: 2m	remaining: 7.69s
940:	learn: 46.3159579	total: 2m	remaining: 7.56s
941:	learn: 46.3058364	total: 2m	remaining: 7.43s
942:	learn: 46.2982025	total: 2m	remaining: 7.31s
943:	learn: 46.2922016	total: 2m 1s	remaining: 7.18s
944:	learn: 46.2805133	total: 2m 1s	remaining: 7.05s
945:	lear

GridSearchCV(cv=3,
             estimator=<catboost.core.CatBoostRegressor object at 0x7f9ec6c244f0>,
             n_jobs=-1,
             param_grid={'depth': [4, 6, 10], 'early_stopping_rounds': [800],
                         'iterations': [1000], 'l2_leaf_reg': [1, 4, 9],
                         'learning_rate': [0.05, 0.1, 0.15]},
             scoring='neg_mean_absolute_percentage_error')

In [22]:
cb_best = cb_b.best_estimator_


In [23]:
cb_best.get_params()

{'iterations': 1000,
 'learning_rate': 0.15,
 'depth': 10,
 'l2_leaf_reg': 9,
 'loss_function': 'RMSE',
 'eval_metric': 'RMSE',
 'random_state': 1602,
 'early_stopping_rounds': 800}

In [24]:
%%time
#это кросс-валидация

params = cb_best.get_params()
cv_dataset = Pool(data=features_train,
                  label=target_train)
scores = cv(cv_dataset,
            params,
            fold_count=2)

Training on fold [0/2]
0:	learn: 476.6482402	test: 475.7836189	best: 475.7836189 (0)	total: 87.6ms	remaining: 1m 27s
1:	learn: 415.5837332	test: 414.7985615	best: 414.7985615 (1)	total: 166ms	remaining: 1m 22s
2:	learn: 364.0336146	test: 363.3420112	best: 363.3420112 (2)	total: 250ms	remaining: 1m 22s
3:	learn: 321.6054542	test: 321.0800780	best: 321.0800780 (3)	total: 376ms	remaining: 1m 33s
4:	learn: 284.7281045	test: 284.3835607	best: 284.3835607 (4)	total: 491ms	remaining: 1m 37s
5:	learn: 254.9470097	test: 254.6521739	best: 254.6521739 (5)	total: 625ms	remaining: 1m 43s
6:	learn: 229.3495071	test: 229.1670190	best: 229.1670190 (6)	total: 812ms	remaining: 1m 55s
7:	learn: 208.9492598	test: 208.8215581	best: 208.8215581 (7)	total: 992ms	remaining: 2m 3s
8:	learn: 192.8241931	test: 192.7380530	best: 192.7380530 (8)	total: 1.45s	remaining: 2m 39s
9:	learn: 178.7639950	test: 178.7313940	best: 178.7313940 (9)	total: 1.64s	remaining: 2m 42s
10:	learn: 168.0449456	test: 168.0620281	best: 

613:	learn: 53.2804369:	learn: 81.7189625	test: 82.5164596	best: 82.5164596 (69)	total: 7.86s	remaining: 1m 44s
43	total: 2m 41s	remaining: 1m 41s
614:	learn: 53.2728115	total: 2m 41s	remaining: 1m 41s
615:	learn: 53.2500478	total: 2m 41s	remaining: 1m 40s
616:	learn: 53.2211370	total: 2m 42s	remaining: 1m 40s
617:	learn: 53.2045409	total: 2m 42s	remaining: 1m 40s
618:	learn: 53.1879985	total: 2m 42s	remaining: 1m 40s
619:	learn: 53.1617209	total: 2m 43s	remaining: 1m 39s
620:	learn: 53.1515602	total: 2m 43s	remaining: 1m 39s
621:	learn: 53.1366518	total: 2m 43s	remaining: 1m 39s
622:	learn: 53.1230106	total: 2m 43s	remaining: 1m 39s
623:	learn: 53.1121395	total: 2m 44s	remaining: 1m 38s
624:	learn: 53.0869543	total: 2m 44s	remaining: 1m 38s
625:	learn: 53.0472954	total: 2m 44s	remaining: 1m 38s
626:	learn: 53.0301599	total: 2m 45s	remaining: 1m 38s
627:	learn: 52.9939291	total: 2m 45s	remaining: 1m 37s
628:	learn: 52.9606495	total: 2m 45s	remaining: 1m 37s
629:	learn: 52.9438336	total

834:	learn: 50.1246052	total: 3m83:	learn: 78.1223320	test: 79.0139754	best: 79.0139754 (83)	total: 9.98s	remaining: 1m 48s
84:	learn: 78.0158800	test: 78.9278264	best: 78.9278264 (84)	total: 10.1s	remaining: 1m 48s
 40s	remaining: 43.6s
835:	learn: 50.1097264	total: 3m 41s	remaining: 43.4s
836:	learn: 50.1022377	total: 3m 41s	remaining: 43.1s
837:	learn: 50.0912988	total: 3m 41s	remaining: 42.9s
838:	learn: 50.0823639	total: 3m 42s	remaining: 42.6s
839:	learn: 50.0660447	total: 3m 42s	remaining: 42.4s
840:	learn: 50.0586473	total: 3m 42s	remaining: 42.1s
841:	learn: 50.0490194	total: 3m 43s	remaining: 41.9s
842:	learn: 50.0384001	total: 3m 43s	remaining: 41.6s
843:	learn: 50.0281807	total: 3m 43s	remaining: 41.4s
844:	learn: 50.0171247	total: 3m 44s	remaining: 41.1s
845:	learn: 50.0105628	total: 3m 44s	remaining: 40.9s
846:	learn: 49.9943120	total: 3m 44s	remaining: 40.6s
847:	learn: 49.9758719	total: 3m 45s	remaining: 40.4s
848:	learn: 49.9650897	total: 3m 45s	remaining: 40.1s
849:	l

86:	learn: 77.6602214	test: 78.5910828	best: 78.5910828 (86)	total: 10.3s	remaining: 1m 47s
87:	learn: 77.5389839	test: 78.4658616	best: 78.4658616 (87)	total: 10.4s	remaining: 1m 47s
88:	learn: 77.1115502	test: 78.0619297	best: 78.0619297 (88)	total: 10.4s	remaining: 1m 46s
89:	learn: 76.8428881	test: 77.8005021	best: 77.8005021 (89)	total: 10.5s	remaining: 1m 46s
90:	learn: 76.6631880	test: 77.6223793	best: 77.6223793 (90)	total: 10.6s	remaining: 1m 45s
91:	learn: 76.4275970	test: 77.3907729	best: 77.3907729 (91)	total: 10.9s	remaining: 1m 47s
92:	learn: 76.1927863	test: 77.1717663	best: 77.1717663 (92)	total: 11s	remaining: 1m 46s
93:	learn: 76.0444174	test: 77.0444006	best: 77.0444006 (93)	total: 11s	remaining: 1m 46s
94:	learn: 75.8627504	test: 76.8731736	best: 76.8731736 (94)	total: 11.1s	remaining: 1m 45s
95:	learn: 75.4943448	test: 76.5146547	best: 76.5146547 (95)	total: 11.2s	remaining: 1m 45s
96:	learn: 75.3733236	test: 76.4136162	best: 76.4136162 (96)	total: 11.3s	remaining:

176:	learn: 64.4681514	test: 66.0846601	best: 66.0846601 (176)	total: 19.3s	remaining: 1m 29s
177:	learn: 64.4117474	test: 66.0365392	best: 66.0365392 (177)	total: 19.4s	remaining: 1m 29s
178:	learn: 64.3206512	test: 65.9722131	best: 65.9722131 (178)	total: 19.5s	remaining: 1m 29s
179:	learn: 64.2568466	test: 65.9104365	best: 65.9104365 (179)	total: 19.6s	remaining: 1m 29s
180:	learn: 64.1540164	test: 65.7966373	best: 65.7966373 (180)	total: 19.7s	remaining: 1m 29s
181:	learn: 64.0831658	test: 65.7380275	best: 65.7380275 (181)	total: 19.8s	remaining: 1m 28s
182:	learn: 64.0476546	test: 65.7118703	best: 65.7118703 (182)	total: 19.8s	remaining: 1m 28s
183:	learn: 63.9758047	test: 65.6441772	best: 65.6441772 (183)	total: 19.9s	remaining: 1m 28s
184:	learn: 63.8993838	test: 65.5664009	best: 65.5664009 (184)	total: 20s	remaining: 1m 28s
185:	learn: 63.8439383	test: 65.5199566	best: 65.5199566 (185)	total: 20.1s	remaining: 1m 28s
186:	learn: 63.7548243	test: 65.4393083	best: 65.4393083 (186)

...

603:	learn: 49.4372505	test: 54.4223805	best: 54.4223805 (603)	total: 1m 4s	remaining: 42.1s
604:	learn: 49.4250811	test: 54.4187813	best: 54.4187813 (604)	total: 1m 4s	remaining: 42s
605:	learn: 49.4118023	test: 54.4151693	best: 54.4151693 (605)	total: 1m 4s	remaining: 41.9s
606:	learn: 49.4021640	test: 54.4084032	best: 54.4084032 (606)	total: 1m 4s	remaining: 41.8s
607:	learn: 49.3855672	test: 54.4057413	best: 54.4057413 (607)	total: 1m 4s	remaining: 41.7s
608:	learn: 49.3736675	test: 54.3983354	best: 54.3983354 (608)	total: 1m 4s	remaining: 41.7s
609:	learn: 49.3518240	test: 54.3888394	best: 54.3888394 (609)	total: 1m 5s	remaining: 41.6s
610:	learn: 49.3334348	test: 54.3723598	best: 54.3723598 (610)	total: 1m 5s	remaining: 41.5s
611:	learn: 49.3159874	test: 54.3634134	best: 54.3634134 (611)	total: 1m 5s	remaining: 41.4s
612:	learn: 49.3011314	test: 54.3523105	best: 54.3523105 (612)	total: 1m 5s	remaining: 41.3s
613:	learn: 49.2859315	test: 54.3503473	best: 54.3503473 (613)	total: 1m

692:	learn: 48.0964410	test: 53.6484480	best: 53.6484480 (692)	total: 1m 14s	remaining: 33.2s
693:	learn: 48.0760844	test: 53.6327419	best: 53.6327419 (693)	total: 1m 15s	remaining: 33.1s
694:	learn: 48.0590059	test: 53.6297969	best: 53.6297969 (694)	total: 1m 15s	remaining: 33s
695:	learn: 48.0364688	test: 53.6223054	best: 53.6223054 (695)	total: 1m 15s	remaining: 32.9s
696:	learn: 48.0278855	test: 53.6146933	best: 53.6146933 (696)	total: 1m 15s	remaining: 32.7s
697:	learn: 48.0154800	test: 53.6102093	best: 53.6102093 (697)	total: 1m 15s	remaining: 32.6s
698:	learn: 48.0050355	test: 53.6023359	best: 53.6023359 (698)	total: 1m 15s	remaining: 32.5s
699:	learn: 47.9918908	test: 53.5971606	best: 53.5971606 (699)	total: 1m 15s	remaining: 32.4s
700:	learn: 47.9770104	test: 53.5938047	best: 53.5938047 (700)	total: 1m 15s	remaining: 32.3s
701:	learn: 47.9576797	test: 53.5811642	best: 53.5811642 (701)	total: 1m 15s	remaining: 32.2s
702:	learn: 47.9485070	test: 53.5783770	best: 53.5783770 (702)

782:	learn: 46.8795961	test: 53.0205056	best: 53.0205056 (782)	total: 1m 25s	remaining: 23.6s
783:	learn: 46.8640460	test: 53.0095722	best: 53.0095722 (783)	total: 1m 25s	remaining: 23.5s
784:	learn: 46.8513877	test: 53.0065566	best: 53.0065566 (784)	total: 1m 25s	remaining: 23.4s
785:	learn: 46.8366374	test: 52.9942965	best: 52.9942965 (785)	total: 1m 25s	remaining: 23.3s
786:	learn: 46.8268298	test: 52.9911357	best: 52.9911357 (786)	total: 1m 25s	remaining: 23.2s
787:	learn: 46.8143714	test: 52.9860388	best: 52.9860388 (787)	total: 1m 25s	remaining: 23.1s
788:	learn: 46.8050105	test: 52.9825845	best: 52.9825845 (788)	total: 1m 25s	remaining: 22.9s
789:	learn: 46.8007477	test: 52.9792273	best: 52.9792273 (789)	total: 1m 25s	remaining: 22.8s
790:	learn: 46.7870377	test: 52.9777862	best: 52.9777862 (790)	total: 1m 26s	remaining: 22.7s
791:	learn: 46.7673471	test: 52.9761769	best: 52.9761769 (791)	total: 1m 26s	remaining: 22.6s
792:	learn: 46.7499073	test: 52.9750854	best: 52.9750854 (79

872:	learn: 45.8532866	test: 52.5720813	best: 52.5720813 (872)	total: 1m 33s	remaining: 13.6s
873:	learn: 45.8377277	test: 52.5570660	best: 52.5570660 (873)	total: 1m 33s	remaining: 13.5s
874:	learn: 45.8243042	test: 52.5490900	best: 52.5490900 (874)	total: 1m 33s	remaining: 13.4s
875:	learn: 45.8153939	test: 52.5466823	best: 52.5466823 (875)	total: 1m 33s	remaining: 13.3s
876:	learn: 45.8010272	test: 52.5438954	best: 52.5438954 (876)	total: 1m 33s	remaining: 13.2s
877:	learn: 45.7841029	test: 52.5344882	best: 52.5344882 (877)	total: 1m 33s	remaining: 13s
878:	learn: 45.7727219	test: 52.5327983	best: 52.5327983 (878)	total: 1m 33s	remaining: 12.9s
879:	learn: 45.7559871	test: 52.5207317	best: 52.5207317 (879)	total: 1m 34s	remaining: 12.8s
880:	learn: 45.7520105	test: 52.5174083	best: 52.5174083 (880)	total: 1m 34s	remaining: 12.7s
881:	learn: 45.7435496	test: 52.5159521	best: 52.5159521 (881)	total: 1m 34s	remaining: 12.6s
882:	learn: 45.7340819	test: 52.5138494	best: 52.5138494 (882)

962:	learn: 44.7569338	test: 52.0245818	best: 52.0245818 (962)	total: 1m 41s	remaining: 3.89s
963:	learn: 44.7484417	test: 52.0187988	best: 52.0187988 (963)	total: 1m 41s	remaining: 3.78s
964:	learn: 44.7370949	test: 52.0147720	best: 52.0147720 (964)	total: 1m 41s	remaining: 3.68s
965:	learn: 44.7227920	test: 52.0136175	best: 52.0136175 (965)	total: 1m 41s	remaining: 3.57s
966:	learn: 44.7074322	test: 52.0068550	best: 52.0068550 (966)	total: 1m 41s	remaining: 3.47s
967:	learn: 44.6900864	test: 52.0038209	best: 52.0038209 (967)	total: 1m 41s	remaining: 3.36s
968:	learn: 44.6798115	test: 52.0005675	best: 52.0005675 (968)	total: 1m 41s	remaining: 3.25s
969:	learn: 44.6672607	test: 51.9972408	best: 51.9972408 (969)	total: 1m 41s	remaining: 3.15s
970:	learn: 44.6551179	test: 51.9919660	best: 51.9919660 (970)	total: 1m 41s	remaining: 3.04s
971:	learn: 44.6479215	test: 51.9907857	best: 51.9907857 (971)	total: 1m 42s	remaining: 2.94s
972:	learn: 44.6376463	test: 51.9884830	best: 51.9884830 (97

In [25]:
predict_data = cb_best.predict(features_test)

In [26]:
df_test_fill.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 110060 entries, 0 to 110059
Data columns (total 14 columns):
 #   Column        Non-Null Count   Dtype              
---  ------        --------------   -----              
 0   year          110060 non-null  int64              
 1   make          110060 non-null  object             
 2   model         110060 non-null  object             
 3   trim          110060 non-null  object             
 4   body          110060 non-null  object             
 5   transmission  110060 non-null  object             
 6   vin           110060 non-null  object             
 7   state         110060 non-null  object             
 8   condition     110060 non-null  float64            
 9   odometer      110060 non-null  float64            
 10  color         110060 non-null  object             
 11  interior      110060 non-null  object             
 12  seller        110060 non-null  object             
 13  saledate      110060 non-null  datetime64[ns

In [27]:
submission = df_test_fill['vin']

In [28]:
predict_series = pd.Series(predict_data)

In [29]:
submission2 = submission.to_frame()

In [30]:
submission2['sellingprice'] = predict_series

In [31]:
submission2.to_csv('sub2.csv', index=False)

In [32]:
submission2.head()

vin  sellingprice
0  1g6dp567450124779    216.516264
1  1gtw7fca7e1902207    798.612669
2  jn8az1mw6dw303497    475.288372
3  2g1wf5e34d1160703    442.146008
4  1n6aa0ec3dn301209    620.320152

In [34]:
submission2['sellingprice'].max()

1228.2888934377117

In [36]:
target_train.max()

1734.0